#### Pour rappel :

In [ ]:
import pandas as pd

In [ ]:
dfr=pd.read_csv("G:/fruits4.csv",sep=";",decimal=",",encoding='latin1')

### Suite du prg de Machine Learning 
#### orange, pêche et raisin, les autres fruits étants rangés dans la catégorie "autre" (initialisation à "autre" par défaut)

In [ ]:
dfr.insert(4,'predicted',"fruit indéterminé")
dfr.insert(5,'actual',"autre")
for i in range(len(dfr)) :
    if (dfr.fruit[i]=="orange") :  dfr.actual[i] = "orange"
    elif (dfr.fruit[i]=="pêche") :  dfr.actual[i] = "pêche"
    elif (dfr.fruit[i]=="raisin") :  dfr.actual[i] = "raisin"

In [ ]:
size_train=0.8
train = dfr.sample(frac=size_train,random_state=1)
print(train.index)
print(train.index[0])
diam_train = train["diametre"]
#X1_train = train["X1"]
#X2_train = train["X2"]
#X3_train = train["X3"]

# Sélectionner tout ce qui n'est pas dans le training set  
# et le mettre dans le jeu de test. Le tilde ~ représente ici le "non logique"
# avec loc on réalise une gestion d'indices

test = dfr.loc[~dfr.index.isin(train.index)]

diam_test = test["diametre"]
#Y_test = test["Y"]
#X1_test = test["X1"]
#X2_test = test["X2"]
#X3_test = test["X3"]

# Affichage des dimensions des 2 sets
print("size_train*271 :",size_train*271)
print("nb values diametre train :",len(diam_train))
print("nb values diametre test :",len(diam_test))
print(train.shape)
#display(train.fruit[2])
print(dfr.shape)
#print(dfr.couleur[1])
diam_test2 = test.diametre
print(diam_test2)

#### Le nouveau coeur de l'algorithme de reconnaissance automatique (mais toujours contraint) des fruits

In [ ]:
controle=0
epsilon=2.54
for i in train.index :
#    train.actual[i] = train.fruit[i]
    #    print("couleur :", train.couleur[i])
#    if (train.couleur[i]=="orange" and train.diametre[i]>=7 and train.diametre[i]<11) :
    if (train.couleur[i]=="orange" and 
        train.diametre[i]>=train[train['fruit'] == "orange"].diametre.mean()
        -epsilon*train[train['fruit'] == "orange"].diametre.std()
        and train.diametre[i]<train[train['fruit'] == "orange"].diametre.mean()
        +epsilon*train[train['fruit'] == "orange"].diametre.std()) :
        train.predicted[i]="orange"
        if (controle==1) : print("le fruit numéro", str(i+1), "est une", train.fruit[i], "de couleur :", train.couleur[i], "de diamètre :", str(train.diametre[i]),"cm")
    elif ((train.couleur[i]=="rouge orangé" or train.couleur[i]=="jaune") and train.diametre[i]>6 and train.diametre[i]<9) :
        if (controle==1) : print("le fruit numéro", str(i+1), "est une pêche de diamère :", str(train.diametre[i]),"cm", "et de couleur :", train.couleur[i])
        train.predicted[i]="pêche"
    elif ((train.couleur[i]=="rouge" or train.couleur[i]=="vert") and train.diametre[i]>0.3 and train.diametre[i]<2) :
        if (controle==1) : print("le fruit numéro", str(i+1), "est du raisin de diamère :", str(train.diametre[i]),"cm", "et de couleur :", train.couleur[i])
        train.predicted[i]="raisin"
    else :
        if (controle==1) : print("couleur :", train.couleur[i],"fruit, diamètre :",train.fruit[i],train.diametre[i],"cm") 
        train.predicted[i]="autre"
if (controle==1) : print(train.fruit)
if (controle==1) : print(train.predicted)
if (controle==2) : 
    for i in train.index : 
        if(train.fruit[i]!=train.predicted[i] and train.actual[i]!="autre"): 
            print("Fruit",i,train.fruit[i],"détecté",train.predicted[i])

#### Evaluation de la performance de l'IA

In [ ]:
from sklearn import metrics
confusion_matrix = pd.crosstab(train.actual, train.predicted, 
                               rownames=['Actual'], colnames=['Predicted'])
print (confusion_matrix)
report_pred=metrics.classification_report(train.actual, train.predicted)
print(report_pred)
print(metrics.accuracy_score(train.actual, train.predicted))
#taux d'erreur 
print(1.0 - metrics.accuracy_score(train.actual, train.predicted))

#### La croisière s'amuse

In [ ]:
n=train.fruit.size
print(n)
#print(train.predicted[2])
print("pour orange, diam moyen :",train[train['fruit'] == "orange"].diametre.mean())
print("pour orange, sigma diam :",train[train['fruit'] == "orange"].diametre.std())
print(train[train['fruit'] == "orange"].diametre)
print(train[train['fruit'] == "orange"])
print(train.groupby('fruit').size())
print(train.groupby('fruit').diametre.mean())
print(len(train))

#### Nouveaux graphes

In [ ]:
train.groupby('fruit').size().plot(kind='pie', autopct='%.1f', legend=True)
train.hist(column="diametre",by="fruit")